# Sujet 1: Concentration de CO2 dans l'atmosphère depuis 1952

In [39]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
#import isomonth
import requests
import os
import urllib.request
data_file = "weekly_in_situ_co2_mlo.csv"
data_url = "https://scrippsco2.ucsd.edu/assets/data/atmospheric/stations/in_situ_co2/weekly/weekly_in_situ_co2_mlo.csv"
if not os.path.exists(data_file):
    urllib.request.urlretrieve(data_url, data_file)

The raw data are rather a mess. The name are not good and are not several lines (with the unity). Hence, the data are stored in a dictionnary with proper keys. Moreover, the date with several format is in the raw data. Only the year and the month is stored. 

Moreover, the data are string and then they are translated as float

In [65]:
raw_data_prov = pd.read_csv('./monthly_in_situ_co2_mlo.csv',skiprows=54)
raw_data = pd.DataFrame({"Year":raw_data_prov['  Yr'][2:].astype(int), "Month":raw_data_prov[' Mn'][2:].astype(int), 
                         "CO2 seasonally":raw_data_prov['     CO2'][2:].astype(float), "CO2 seasonally adjust":raw_data_prov['seasonally'][2:].astype(float),
                         "seasonally fit":raw_data_prov['        fit'][2:].astype(float),"seasonally adjusted fit":raw_data_prov['  seasonally'][2:].astype(float), 
                         "CO2 seasonally filled":raw_data_prov['      CO2'][2:].astype(float), "CO2 seasonally adjust filled":raw_data_prov[' seasonally'][2:].astype(float)})
#raw_data = raw_data.drop([0,1])
raw_data


CO2 seasonally  CO2 seasonally adjust  CO2 seasonally adjust filled  \
2            -99.99                 -99.99                        -99.99   
3            -99.99                 -99.99                        -99.99   
4            315.70                 314.43                        314.43   
5            317.45                 315.16                        315.16   
6            317.51                 314.71                        314.71   
7            -99.99                 -99.99                        315.14   
8            315.86                 315.19                        315.19   
9            314.93                 316.19                        316.19   
10           313.21                 316.09                        316.09   
11           -99.99                 -99.99                        315.41   
12           313.33                 315.20                        315.20   
13           314.67                 315.43                        315.43   
14           315.58                 315.54                        315.54   
15           316.49                 315.86                        315.86   
16           316.65                 315.38                        315.38   
17           317.72                 315.41                        315.41   
18           318.29                 315.48                        315.48   
19           318.15                 316.03                        316.03   
20           316.54                 315.87                        315.87   
21           314.80                 316.07                        316.07   
22           313.84                 316.73                        316.73   
23           313.33                 316.33                        316.33   
24           314.81                 316.68                        316.68   
25           315.58                 316.35                        316.35   
26           316.43                 316.39                        316.39   
27           316.98                 316.35                        316.35   
28           317.58                 316.28                        316.28   
29           319.03                 316.70                        316.70   
30           320.04                 317.21                        317.21   
31           319.58                 317.47                        317.47   
..              ...                    ...                           ...   
728          408.90                 408.09                        408.09   
729          407.10                 408.63                        408.63   
730          405.59                 409.08                        409.08   
731          405.99                 409.61                        409.61   
732          408.12                 410.38                        410.38   
733          409.23                 410.15                        410.15   
734          410.92                 410.87                        410.87   
735          411.66                 410.90                        410.90   
736          412.00                 410.46                        410.46   
737          413.52                 410.73                        410.73   
738          414.83                 411.43                        411.43   
739          413.96                 411.39                        411.39   
740          411.85                 411.04                        411.04   
741          410.08                 411.62                        411.62   
742          408.55                 412.05                        412.05   
743          408.43                 412.06                        412.06   
744          410.29                 412.55                        412.55   
745          411.85                 412.78                        412.78   
746          413.37                 413.32                        413.32   
747          414.09                 413.33                        413.33   
748          414.51                 412.94           

According to the authors:

"CO2 seasonally" gives monthly Mauna Loa CO2 concentrations in micro-mol CO2 per mole (ppm), reported on the 2008A SIO manometric mole fraction scale.The monthly values have been adjusted to 24:00 hours on the 15th of each month.

"CO2 seasonally adjust" gives the same data after a seasonal adjustment to remove the quasi-regular seasonal cycle.  The adjustment involves subtracting from the data a 4-harmonic fit with a linear gain factor.

"seasonally fit" is a smoothed version of the data generated from a stiff cubic spline function plus 4-harmonic functions with linear gain.

"seasonally adjusted fit" is the same smoothed version with the seasonal cycle removed.  

"CO2 seasonally adjust filled" and "CO2 seasonally filled" are identical to Columns "CO2 seasonally" and "CO2 seasonally adjust" except that the missing values from have been filled with values from Columns "fit" and "seasonally adjusted fit"

Moreover, it is said that the missing data are completed with the value -99.99

The month and year can be then converted to panda Period 

In [69]:
raw_data['period'] = [pd.Period(str(y)+'-'+str(m)+'-15') for y,m in zip(raw_data['Year'],raw_data['Month'])]
sorted_data = raw_data.set_index('period').sort_index()

In order to highlight the seasonal and interannual variations, only the raw concentrations stored in 'CO2 seasonally" and "CO2 seasonally adjust" are enough. The first one is the raw concentrations and contains both the seasonal and interannual variations. The second one is a adjustement made in order to get rid of the seasonal variations.

In [ ]:
nb_year = 10
sorted_data=sorted_data[~(sorted_data["CO2 seasonally"] < 0)]
sorted_data["CO2 seasonally"][-12*nb_year:].plot(label='raw data')
sorted_data["CO2 seasonally adjust"][-12*nb_year:].plot(label='interannual variation')
sorted_data=sorted_data[~(sorted_data["seasonally fit"] < 0)]
sorted_data["seasonally fit"][-12*nb_year:].plot(label='smoothed data')
plt.plot([sorted_data["period"][-12*nb_year],sorted_data["period"][-1]],[sorted_data["CO2 seasonally adjust"][-12*nb_year],sorted_data["CO2 seasonally adjust"][-1]])
plt.legend()
#sorted_data = data.set_index('period').sort_index()

We store the difference between the monthly CO2 concentration and the interannual variations of this concentration (obtained by the adjustement). Hence, it represent the seasonnal variations of the concentration 

In [ ]:
sorted_data["CO2 seasonal variations"] = sorted_data["CO2 seasonally"] - sorted_data["CO2 seasonally adjust"]
sorted_data["CO2 seasonal variations"][-12*nb_year:].plot()

This seasonal variations are rather close to a cosinus function with a one year period. In the other hand, the interannual variations are nearly linear. A FAIRE : une régression linéaire pour montrer la proximité et la pente 